## Import essential libraries

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import folium
import geopandas as gpd
from shapely.geometry import LineString
from tqdm.notebook import tqdm

import plotly.graph_objects as go

## Read and process data

In [2]:
df = pd.read_csv("Data\Bornholmsgat_26_2_2022.csv", parse_dates=[0]) #.iloc[:, :8]
df = df.drop("Trip No.", axis=1)
df = df.sort_values(by="# Timestamp", ascending=True)
df.info()
df.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 581026 entries, 0 to 581025
Data columns (total 12 columns):
 #   Column       Non-Null Count   Dtype         
---  ------       --------------   -----         
 0   # Timestamp  581026 non-null  datetime64[ns]
 1   MMSI         581026 non-null  int64         
 2   Latitude     581026 non-null  float64       
 3   Longitude    581026 non-null  float64       
 4   SOG          546066 non-null  float64       
 5   COG          537114 non-null  float64       
 6   Heading      478677 non-null  float64       
 7   IMO          581026 non-null  int64         
 8   Name         541316 non-null  object        
 9   Ship type    581026 non-null  object        
 10  Length       522420 non-null  float64       
 11  Draught      475722 non-null  float64       
dtypes: datetime64[ns](1), float64(7), int64(2), object(2)
memory usage: 57.6+ MB


# Timestamp       MMSI   Latitude  Longitude   SOG    COG  Heading  IMO  \
0   2022-02-26    2655130  55.668072  14.158132   NaN    NaN      NaN    0   
10  2022-02-26  265695200  55.474810  14.285658   0.0    0.0      NaN    0   
9   2022-02-26  538007571  55.418290  14.735065  12.8   63.0     63.0    0   
7   2022-02-26  215584000  55.261583  14.453747  11.0   35.0     37.0    0   
6   2022-02-26  265750000  55.556388  14.359113   0.0  293.5    349.0    0   

   Name  Ship type  Length  Draught  
0   NaN  Undefined     NaN      NaN  
10  NaN  Undefined     NaN      NaN  
9   NaN  Undefined     NaN      NaN  
7   NaN  Undefined     NaN      NaN  
6   NaN  Undefined     NaN      NaN

## Functions for analysis

Ship that was identified as sailing with dragged anchors due to which it caused damage to the power cable in Bornholm

- Vessel:SAMUS SWAN 
- MMSI: 248363000
- Type: Oil/Chemical Tanker
- IMO: 9401312

In [3]:
def plot_ship_routes_plotly(df, ship_ids):

    fig = go.Figure()
    
    for mmsi in ship_ids:
        ais_data = df[df["MMSI"]==mmsi]
        
        fig.add_trace(go.Scattermapbox(
            lon = ais_data["Longitude"],
            lat = ais_data["Latitude"],
            showlegend = False,
            hovertemplate = "%{text}",
            text = ais_data["# Timestamp"],
            name = mmsi,
            marker="lines"
        ))

    fig.update_layout(
        mapbox=dict(
            style="open-street-map",
            center = dict(lat=55.354138, lon=14.4997),
            zoom=6
        )
    )

    return fig

def make_paths(ais_df):
    path = {}
    for mmsi, dfx in ais_df.dropna(subset=["Latitude", "Longitude"]).groupby("MMSI"):
        points = list(zip(dfx["Longitude"], dfx["Latitude"]))
        if len(points)>1:
            path[mmsi] = LineString(points)
        else:
            print("Only %d point found for the ship with MMSI: %d" % (len(points), mmsi))
            
    path_gdf = gpd.GeoDataFrame({"MMSI":path.keys(), "geometry": path.values()}, crs="epsg:4326", geometry="geometry")
    return path_gdf

def plot_ship_routes_folium(df):
    
    path_gdf = make_paths(df)
    
    route_map = folium.Map(location = (55.354138,14.4997), zoom_start=8)

    for mmsi in tqdm(path_gdf["MMSI"]):
        x = path_gdf[path_gdf["MMSI"]==mmsi]
        x = x.to_json()
        folium.GeoJson(x, tooltip="MMSI: %d" % mmsi).add_to(route_map)
        
    return route_map


def line_style(x):
    return {
        "opacity": 1 if x["properties"]["MMSI"] ==  MMSI else 0.1,
        "color": "red" if x["properties"]["MMSI"] == MMSI else "blue"
    }

def time_series_profile(df, parameter="COG"):
    figure = go.Figure()
    for mmsi, dfx in df.groupby("MMSI"):
        figure.add_trace(go.Scatter(
            y=dfx[parameter],
            name=mmsi,
            mode = "lines"
        ))
    figure.update_layout(
        title=f"Time series of {parameter}",
        yaxis = dict(title=parameter),
        xaxis = dict(title="Unit Time")
    )
    return figure

## Analysis

### Compare ship routes

- provide random colors to each ships

In [4]:
ship_df = df[df["MMSI"].isin([248363000, 257206000])]
plot_ship_routes_folium(ship_df)

  0%|          | 0/2 [00:00<?, ?it/s]

### Compare the timeseries of a ship parameter

[Text formating in plotly](https://plotly.com/python/hover-text-and-formatting/)

In [5]:
time_series_profile(ship_df)

## Ship wavy path detection

In [6]:
from zig_zag_ship import detect_zigzag_motion, ship_zigzag_analysis_report

In [7]:
samus = df[df["MMSI"]==248363000]
wave_list, wave_score = detect_zigzag_motion(samus)
wave_score

0.7240791268758526

In [8]:
ship_zigzag_analysis_report(samus)

## Top 10 ships with zigzag motion

In [38]:
%%time
zscores = {}
for mmsi, dfx in tqdm(df.groupby("MMSI"), unit=" ship"):
    _, score = detect_zigzag_motion(dfx)
    zscores[mmsi] = [score]

  0%|          | 0/292 [00:00<?, ? ship/s]

Wall time: 3.64 s


In [40]:
zscore_report = pd.DataFrame.from_dict(zscores, orient="index", columns=["score"]).reset_index()
zscore_report.rename(columns={"index":"MMSI"}, inplace=True)
z1 = zscore_report.sort_values(by="score", ascending=False).head(10)
z1

MMSI     score
274  376532000  0.827273
266  305922000  0.780426
168  248363000  0.724079
112  229536000  0.711129
186  257206000  0.538499
164  246855000  0.489964
141  244613000  0.451308
42   219000167  0.318750
204  265019000  0.219766
200  261003230  0.216389

### Plotting the top 10 zigzag ships

In [42]:
# ship_df = df[df["MMSI"].isin(z1["MMSI"])]
ship_df = df[df["MMSI"]==219000167]
plot_ship_routes_folium(ship_df)

  0%|          | 0/10 [00:00<?, ?it/s]

In [43]:
time_series_profile(ship_df)